## Introduction

This notebook trains, tunes, and backtests an ML-driven **Double-Barrier (first-hit) strategy** by default.  
Labels are standardized to **0/1/2** → *(0 = down / lower barrier hit, 1 = flat / no hit within horizon, 2 = up / upper barrier hit)*, and predictions are mapped to trading signals **−1/0/+1** for backtesting.

### What’s included
- **Labeling (default):** `create_labels_double_barrier(up=THRESHOLD, down=THRESHOLD, horizon=HORIZON)` from `labeling_schemes.py`.
- **Modeling:** classifiers output **{0,1,2}**; we compare directly against the label **{0,1,2}** space (no shifts).
- **Backtesting:** quick vectorized metrics (Sharpe, win-rate) and a **VectorBT long/short** portfolio.
- **Metrics:** optional **annualized Sharpe** via `periods_per_year`.

### Switching strategies
You can use any other labeling function from `labeling_schemes.py` (or add your own).  
To switch, replace the Double-Barrier call in these places with your chosen labeler and its column name:

1. **Part 1 – Feature/Label Prep:**  
   Replace  
   `create_labels_double_barrier(...) → label_col = "barrier_label"`  
   with your function, e.g.  
   `create_labels_multi_bar(...) → label_col = "multi_bar_label"`.

2. **Part 2 – VectorBT Backtest:**  
   Use the same labeler as in Part 1 and set `y012 = df_lbl[label_col].astype(int)` before predicting.

3. **Part 3 – Optuna Tuning:**  
   In `prepare_dataset(...)`, use your labeler and return `y012` from the corresponding label column. The TSCV objective stays in **0/1/2**.

> **Tips**
> - Treat **1 = flat** as “no position”; only **0/2** map to short/long.
> - Avoid look-ahead: features at *t*, labels at *t+H* (or first-hit within the horizon).
> - Interactive VectorBT charts won’t render on GitHub—run locally to view.


In [ ]:

import warnings
warnings.filterwarnings("ignore")

import os, sys, time, threading
from pathlib import Path
import numpy as np
import pandas as pd
import joblib
import plotly.graph_objects as go

from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.naive_bayes import GaussianNB, BernoulliNB
from sklearn.metrics import accuracy_score
from sklearn.model_selection import TimeSeriesSplit

from ctrader_client import start_background, wait_until_symbols_loaded, get_ohlc_df
from feature_engineering import add_core_features, get_core_feature_cols
from labeling_schemes import  create_labels_double_barrier
import bt_core
from importlib import reload
reload(bt_core)


[BOOT] host_type = demo
[BOOT] account_id = 44015421
[BOOT] token_len = 43
[BOOT] token_head = LsMFXxrW_0TU
[BOOT] client_id_head = 16209_oM


<module 'bt_core' from 'c:\\Users\\moham\\OneDrive\\Github\\ml-double-barrier-strategy2\\bt_core.py'>

## Part 1 — Data & Feature Engineering + Model Selection & Save

**What this section does**

- Fetches OHLCV from cTrader for the configured symbols/timeframe.
- Builds core technical features and creates **double-barrier labels (0/1/2)**.
- Runs **time-series cross-validation** with `cv_quick`, reporting **Accuracy** and **annualized Sharpe** from a quick backtest.
- Selects the best model **per symbol**, refits on all available data, and **persists** the pipeline and feature list to `models/<tf>_models/`.

**Inputs**
- Symbols & timeframe (e.g., `EURUSD`, `H1`), cTrader credentials, lookback window.
- Feature config (which indicators to compute) and labeling params (`up/down/horizon`).

**Outputs**
- Trained pipeline per symbol (`.pkl`) + feature list (`.json`) in `models/<tf>_models/`.
- CV summary table with mean **Accuracy** and **Sharpe**.

**Flow**
1. Download candles → assemble features → align labels (no look-ahead).
2. CV with expanding time splits → pick top Sharpe (tie-break by Accuracy).
3. Refit best model on full data → save artifacts.

> Tip: set `periods_per_year` to match your timeframe for Sharpe:
> `D1 ≈ 252`, `H4 ≈ 6*252`, `H1 ≈ 24*252`, `M15 ≈ 96*252`.


In [2]:

symbols = ["EURUSD", "GBPUSD", "AUDUSD"]
timeframe_str = "H1"
n_bars = 20000
horizon = 5
threshold = 0.005

freq_mapping = {"M1":"1min","M5":"5min","M15":"15min","M30":"30min","H1":"1h","H4":"4h","D1":"1D","W1":"1W"}
freq_str = freq_mapping.get(timeframe_str, "1h")

model_folder = Path(f"models/{timeframe_str.lower()}_models")
model_folder.mkdir(parents=True, exist_ok=True)

start_background()
wait_until_symbols_loaded(timeout=20)

raw_data = {}
for sym in symbols:
    try:
        df = get_ohlc_df(sym, timeframe_str, n_bars)
        if df.empty:
            print(f"⚠️ No data for {sym}, skipping...")
            continue
        if "volume" not in df.columns and "tick_volume" in df.columns:
            df = df.rename(columns={"tick_volume": "volume"})
        raw_data[sym] = df
        print(f"✅ {sym}: {len(df)} rows")
    except Exception as e:
        print(f"⚠️ {sym}: fetch failed — {e}")


[AUTH] token has accounts: [41761724, 44015421, 44089601]
[AUTH] OK: ACCOUNT_ID 44015421 is authorized by token.
[DEBUG] Loaded 6266 symbols (e.g. [(1, 'EURUSD'), (3, 'EURJPY'), (18, 'AUDCAD')])
✅ EURUSD: 6187 rows
✅ GBPUSD: 6187 rows
✅ AUDUSD: 6187 rows


In [ ]:
# ----------------------------------------------------------------------------
# 3) FEATURE ENGINEERING + LABELING → X, y per symbol
# ----------------------------------------------------------------------------
core_feature_cols = get_core_feature_cols()
prepared = {}   # {symbol: {"X": DataFrame, "y": Series (0/1/2), "close": Series}}

for sym, df in raw_data.items():
    # --- core features ---
    feats = add_core_features(df)

    # --- choose ONE labeling scheme ---
    # Option A: multi-bar (−1/0/+1 on future return)
    # lbl = create_labels_multi_bar(feats, horizon=horizon, threshold=threshold)
    # label_col = "multi_bar_label"

    # Option B: double-barrier (−1/0/+1 on first barrier hit)
    lbl = create_labels_double_barrier(feats, up=threshold, down=threshold, horizon=horizon)
    label_col = "barrier_label"

    # --- align & select features ---
    X = lbl[core_feature_cols].dropna()
    y = lbl.loc[X.index, label_col].astype(int)
    close = lbl.loc[X.index, "close"].astype(float)

    if len(X) < 200:  # simple sanity check
        print(f"⚠️ {sym}: not enough rows after FE/labels ({len(X)}) — skipping")
        continue

    prepared[sym] = {"X": X, "y": y, "close": close}

print(f"\n📦 Prepared datasets: {len(prepared)} symbols ready.")


📦 Prepared datasets: 3 symbols ready.


In [4]:

def model_registry():
    return {
        "RandomForestClassifier": Pipeline([("scaler", StandardScaler()), ("clf", RandomForestClassifier(n_estimators=200, random_state=42))]),
        "GradientBoostingClassifier": Pipeline([("scaler", StandardScaler()), ("clf", GradientBoostingClassifier(n_estimators=200, learning_rate=0.05, max_depth=3, random_state=42))]),
        "SVC": Pipeline([("scaler", StandardScaler()), ("clf", SVC(C=1.0, kernel="rbf", probability=True, random_state=42))]),
        "XGBClassifier": Pipeline([("scaler", StandardScaler()), ("clf", XGBClassifier(
            n_estimators=300, learning_rate=0.05, max_depth=5, subsample=0.9, colsample_bytree=0.9,
            objective="multi:softprob", num_class=3, eval_metric="mlogloss", random_state=42
        ))]),
        "LGBMClassifier": Pipeline([("scaler", StandardScaler()), ("clf", LGBMClassifier(
            n_estimators=300, learning_rate=0.05, max_depth=-1, subsample=0.9, colsample_bytree=0.9,
            objective="multiclass", num_class=3, random_state=42
        ))]),
        "GaussianNB": Pipeline([("scaler", StandardScaler()), ("clf", GaussianNB())]),
        "BernoulliNB": Pipeline([("scaler", StandardScaler()), ("clf", BernoulliNB())]),
    }


In [5]:

from bt_core import cv_quick
all_results, best_models = [], {}
annualizer = 24*252 if timeframe_str.upper().startswith("H") else None

for symbol, pack in prepared.items():
    print(f"\n\n🔵 Processing Symbol: {symbol}")
    X, y, close = pack["X"], pack["y"], pack["close"]
    models = model_registry()
    cv_rows = cv_quick(models=models, X=X, y_shifted=y, close=close, n_splits=5, threshold=0.0, fees=0.0002, periods_per_year=annualizer)
    for row in cv_rows:
        row["Symbol"] = symbol
    all_results.extend(cv_rows)

    sym_df = pd.DataFrame(cv_rows)
    if sym_df["Sharpe"].isna().all():
        print(f"⚠️ {symbol}: all Sharpe NaN — skipping")
        continue

    best_row = sym_df.sort_values("Sharpe", ascending=False).iloc[0]
    best_name = best_row["Model"]
    pipe = model_registry()[best_name]
    pipe.fit(X, y)
    best_models[symbol] = {"Model": best_name, "Pipeline": pipe}
    print(f"🏆 Best for {symbol}: {best_name} (Sharpe={best_row['Sharpe']:.2f})")

for symbol, info in best_models.items():
    save_path = model_folder / f"{symbol}_{timeframe_str}_best_model.pkl"
    joblib.dump({"pipeline": info["Pipeline"], "features": core_feature_cols, "timeframe": timeframe_str}, save_path)
    print(f"✅ Saved best model for {symbol} ({timeframe_str}) to {save_path}")




🔵 Processing Symbol: EURUSD
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000345 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3558
[LightGBM] [Info] Number of data points in the train set: 1027, number of used features: 16
[LightGBM] [Info] Start training from score -4.536502
[LightGBM] [Info] Start training from score -0.010769
[LightGBM] [Info] Start training from score -34.538776
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

In [8]:
summary_df = pd.DataFrame(all_results).sort_values(by=["Symbol","Sharpe"], ascending=[True, False])
if not summary_df.empty:
    pivot = summary_df.pivot(index="Model", columns="Symbol", values="Sharpe").round(2)
    fig = go.Figure(data=go.Heatmap(z=pivot.values, x=pivot.columns, y=pivot.index, colorscale='RdYlGn', zmid=0.0))
    for i, m in enumerate(pivot.index):
        for j, s in enumerate(pivot.columns):
            v = pivot.iloc[i, j]
            if pd.notna(v):
                fig.add_annotation(x=s, y=m, text=f"{v:.2f}", showarrow=False,
                                   font=dict(color='white' if abs(v) > 0.5 else 'black', size=11))
    fig.update_layout(title="Sharpe per Model per Symbol (Quick CV)", width=1200, height=600)
    fig.show()
else:
    print("No summary to display.")

# =========================
# 2) Interactive Table (robust to missing columns)
# =========================
desired = ["Symbol", "Model", "Accuracy", "Return(%)", "Sharpe"]
present = [c for c in desired if c in summary_df.columns]  # only keep what exists
tbl = summary_df[present].copy()

# pretty formatting for columns that exist
def fmt(col, ndigits):
    if col in tbl.columns:
        tbl[col] = pd.to_numeric(tbl[col], errors="coerce").round(ndigits)
fmt("Accuracy", 3)
fmt("Sharpe", 3)
fmt("Return(%)", 2)

fig2 = go.Figure(
    data=[go.Table(
        header=dict(values=list(tbl.columns), fill_color='#C6F7F7', align='left', font=dict(size=12, color='black')),
        cells=dict(values=[tbl[c] for c in tbl.columns], fill_color='#ECECFF', align='left', font=dict(size=12))
    )]
)
fig2.update_layout(title="Model Performance Summary (Quick CV)", width=1400, height=450)
fig2.show()

# =========================
# 3) Exports (CSV / Excel if available)
# =========================
try:
    from IPython.display import display, FileLink
    tbl.to_csv("model_summary.csv", index=False)
    display(FileLink("model_summary.csv"))
    try:
        with pd.ExcelWriter("model_summary.xlsx", engine="xlsxwriter") as w:
            tbl.to_excel(w, index=False, sheet_name="Summary")
        display(FileLink("model_summary.xlsx"))
    except Exception:
        pass
except Exception:
    pass

# Streamlit (no-op if not running Streamlit)
try:
    import streamlit as st, io
    st.markdown("### Download Table")
    st.download_button("Download CSV", data=tbl.to_csv(index=False), file_name="model_summary.csv", mime="text/csv")
    bio = io.BytesIO()
    with pd.ExcelWriter(bio, engine="xlsxwriter") as w:
        tbl.to_excel(w, index=False, sheet_name="Summary")
    st.download_button("Download Excel", data=bio.getvalue(),
                       file_name="model_summary.xlsx",
                       mime="application/vnd.openxmlformats-officedocument.spreadsheetml.sheet")
except Exception:
    pass


c:\Users\moham\OneDrive\Github\ml-double-barrier-strategy2\model_summary.csv

2025-08-21 18:51:31.965 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.965 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.965 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.969 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.971 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.973 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.974 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-08-21 18:51:31.975 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bar

## Part 2 — VectorBT Backtesting (Deep)

**What this section does**

- Loads the saved best pipeline per symbol and recomputes features on **fresh data**.
- Produces predictions in **0/1/2** and maps them to **trading signals −1/0/+1**.
- Runs a **VectorBT long/short portfolio** (with fees) and plots the equity curve.
- Prints key metrics (**Total Return, Sharpe, Max Drawdown**) and builds a summary table.

**Inputs**
- Saved model path (e.g., `models/<tf>_models/`), fresh OHLCV (`close` aligned to features).
- Backtest params: `init_cash`, `freq` (e.g., `"1h"`), `fees`, `periods_per_year`.

**Outputs**
- `vbt.Portfolio` object with long & short legs, performance table, and charts.
- Per-symbol metrics (Total Return, Sharpe, MDD) + consolidated summary.

**Flow**
1. Load pipeline → recompute features → `predict` → labels **{0,1,2}**.
2. Convert labels → signals using `labels012_to_signals(…)` (0→−1, 1→0, 2→+1).
3. Call `vbt_backtest_from_signals(…)` to build the portfolio and plot results.

> Tips:  
> • Ensure index alignment (`close` and signals share the same timestamps).  
> • Drop/shift warm-up rows where indicators/labels are `NaN`.  
> • Set `periods_per_year` to match your timeframe for annualized Sharpe (e.g., `H1 ≈ 24*252`).  


In [ ]:
# =====================================
# Part 2 — VectorBT Backtesting (cTrader)
# =====================================

# --- Setup
import warnings, time, threading
from pathlib import Path
import numpy as np
import pandas as pd
import joblib
import vectorbt as vbt
import plotly.graph_objects as go
from sklearn.metrics import confusion_matrix
from pathlib import Path
warnings.filterwarnings("ignore")

from ctrader_client import init_client, get_ohlc_data, symbol_name_to_id
from feature_engineering import add_core_features
from labeling_schemes import create_labels_double_barrier
from twisted.internet import reactor  # used to check/start service

# ---------- Config ----------
symbols = ["EURUSD", "GBPUSD", "AUDUSD"]   # extend as needed
tf = "H1"                                  # "M1","M5","M15","M30","H1","H4","D1"
n_bars = 5000
horizon = 5
threshold = 0.005
fees = 0.0002
init_cash = 10_000
model_folder = Path(f"models/{tf.lower()}_models")  # auto-matches Part 1

# TF → vectorbt freq
freq_map = {"M1":"1min","M5":"5min","M15":"15min","M30":"30min","H1":"1h","H4":"4h","D1":"1D"}
freq_str = freq_map.get(tf, "1h")

# ---------- Start cTrader once ----------
if not reactor.running:
    threading.Thread(target=init_client, daemon=True).start()

# wait for symbol map bootstrap (up to ~20s)
for _ in range(200):
    if symbol_name_to_id:
        break
    time.sleep(0.1)
else:
    raise RuntimeError("cTrader client started, but symbols failed to load in time.")

# ---------- helpers ----------
def load_model_bundle(path: Path):
    """Accept both {'pipeline', 'features'} and legacy {'model','scaler','features'} bundles."""
    b = joblib.load(path)
    if "pipeline" in b:
        return dict(kind="pipeline", pipeline=b["pipeline"], features=b.get("features"))
    if "model" in b and "scaler" in b:
        return dict(kind="legacy", model=b["model"], scaler=b["scaler"], features=b.get("features"))
    raise ValueError(f"Unrecognized model bundle: {path}")

def candles_to_df(candles: list[dict]) -> pd.DataFrame:
    df = pd.DataFrame(candles)
    df["time"] = pd.to_datetime(df["time"], utc=True)
    df.set_index("time", inplace=True)
    return df[["open","high","low","close","volume"]].rename(columns={"volume":"tick_volume"})

def to_signals(preds: np.ndarray) -> np.ndarray:
    """Map {0,1,2} → {-1,0,+1}; if already in {-1,0,+1}, return as-is."""
    preds = np.asarray(preds)
    uniq = set(np.unique(preds))
    return preds - 1 if uniq.issubset({0,1,2}) else preds.astype(int)

def print_full_vbt_summary(symbol: str, pf, acc: float):
    ret = float(pf.total_return())
    sr  = float(pf.sharpe_ratio())
    print(f"\n✅ Full Backtest Results for {symbol}:")
    print(f"Accuracy={acc:.2f}, Return={ret:.2f}%, Sharpe={sr:.2f}")
    print(pf.stats())

def plot_actual_vs_predicted_close(symbol: str, close: pd.Series, preds: np.ndarray, *, horizon: int = 5, step: float = 0.001):
    """Purely visual ‘predicted close’ path, shifted by horizon and nudged by signals."""
    actual_close = close.copy()
    predicted_close = actual_close.copy()
    for i in range(len(predicted_close) - horizon):
        window = preds[i: i + horizon]
        predicted_close.iloc[i + horizon] = predicted_close.iloc[i] * (1 + step * window.sum())
    predicted_close = predicted_close.shift(-horizon)

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=actual_close.index, y=actual_close, name="Actual Close",
                             mode="lines", line=dict(width=2, color="black")))
    fig.add_trace(go.Scatter(x=predicted_close.index, y=predicted_close, name="Predicted Close",
                             mode="lines", line=dict(width=4, color="#ff9900")))
    fig.update_layout(
        title=f"📈 Actual vs Predicted Close Price (horizon={horizon}) for {symbol}",
        xaxis_title="Date", yaxis_title="Price", template="plotly_white",
        height=700, legend=dict(orientation="h")
    )
    fig.show()

# ---------- Backtest loop ----------
all_rows = []

for symbol in symbols:
    print(f"\n🔵 Backtesting: {symbol}")

    bundle_path = Path(model_folder) / f"{symbol}_{tf}_best_model.pkl"
    if not bundle_path.exists():
        print(f"⚠️ No model for {symbol} at {bundle_path}, skipping.")
        continue

    bundle = load_model_bundle(bundle_path)

    # fetch candles
    try:
        raw = get_ohlc_data(symbol, tf=tf, n=n_bars)
        df = candles_to_df(raw["candles"])
    except Exception as e:
        print(f"⚠️ Data fetch failed for {symbol}: {e}")
        continue

    # features + labels
    df_feat = add_core_features(df.copy())
    df_lbl  = create_labels_double_barrier(df_feat, up=threshold, down=threshold, horizon=horizon)

    # feature set to use
    core_cols = [
        "sma_20","ema_20","kama_10","rsi_14","macd_diff",
        "atr_14","obv","rolling_std_20","spread","fill","amplitude",
        "autocorr_1","autocorr_5","autocorr_10","market_regime","stationary_flag"
    ]
    use_cols = bundle.get("features") or [c for c in core_cols if c in df_lbl.columns]

    X = df_lbl[use_cols].dropna()
    close = df_lbl.loc[X.index, "close"]

    # --- NEW: labels already 0/1/2 after your patch
    y012 = df_lbl.loc[X.index, "barrier_label"].astype(int)

    # --- predictions
    if bundle["kind"] == "pipeline":
        preds_012 = bundle["pipeline"].predict(X)     # {0,1,2}
    else:
        X_scaled = bundle["scaler"].transform(X)
        preds_012 = bundle["model"].predict(X_scaled)
    preds = to_signals(preds_012)                     # {-1,0,+1}

    # accuracy in the {0,1,2} space
    acc = float((preds_012 == y012).mean())

    # --- vectorbt portfolio (long-only entries/exits as in original)
    sig = pd.Series(preds, index=close.index)
    
    # Allow both long and short legs based on signal sign transitions
    long_entries  = (sig.shift(1).fillna(0) <= 0) & (sig > 0)
    long_exits    = sig <= 0
    short_entries = (sig.shift(1).fillna(0) >= 0) & (sig < 0)
    short_exits   = sig >= 0

    pf = vbt.Portfolio.from_signals(
        close=close,
        entries=long_entries,
        exits=long_exits,
        short_entries=short_entries,
        short_exits=short_exits,
        init_cash=init_cash,
        freq=freq_str,
        fees=fees,
    )


    # metrics & diagnostics
    total_ret = float(pf.total_return())              # decimal (0.1769 = 17.69%)
    sharpe    = float(pf.sharpe_ratio())
    max_dd    = float(pf.max_drawdown())
    cm = confusion_matrix(y012, preds_012, labels=[0,1,2])

    print(f"✅ {symbol}: acc={acc:.3f} | ret={total_ret:.2%} | sharpe={sharpe:.2f} | maxDD={max_dd:.2%}")
    print("Confusion matrix (rows=true, cols=pred, order [0,1,2]):\n", cm)

    # full summary + plots
    print_full_vbt_summary(symbol, pf, acc)
    pf.plot(title=f"{symbol} — VectorBT Backtest ({tf})").show()
    plot_actual_vs_predicted_close(symbol, close, preds, horizon=horizon, step=0.001)

    model_name = (
        bundle["pipeline"].steps[-1][1].__class__.__name__
        if bundle["kind"] == "pipeline" else bundle["model"].__class__.__name__
    )
    all_rows.append(dict(
        Symbol=symbol,
        Model=model_name,
        Accuracy=acc,
        ReturnPct=total_ret * 100.0,
        Sharpe=sharpe,
        MaxDDPct=max_dd * 100.0
    ))

# ---------- Summary visuals ----------
summary_df = pd.DataFrame(all_rows).sort_values("Sharpe", ascending=False)

if not summary_df.empty:
    # Heatmap
    piv = summary_df.pivot(index="Model", columns="Symbol", values="Sharpe")
    ann = piv.round(2)
    fig = go.Figure(data=go.Heatmap(
        z=piv.values, x=piv.columns, y=piv.index,
        colorscale="RdYlGn", zmid=0.0, colorbar=dict(title="Sharpe"),
        hovertemplate='Model: %{y}<br>Symbol: %{x}<br>Sharpe: %{z:.3f}<extra></extra>'
    ))
    for i, m in enumerate(ann.index):
        for j, s in enumerate(ann.columns):
            v = ann.iloc[i, j]
            if pd.notna(v):
                fig.add_annotation(x=s, y=m, text=f"{v:.2f}", showarrow=False,
                                   font=dict(color="black" if abs(v) < 0.5 else "white", size=11))
    fig.update_layout(title="Sharpe per Model per Symbol (VectorBT Backtest)",
                      xaxis_title="Symbol", yaxis_title="Model", width=1300, height=600)
    fig.show()

    # Interactive table
    tbl = summary_df.rename(columns={"ReturnPct":"Return(%)","MaxDDPct":"MaxDD(%)"}).copy()
    for c, d in [("Accuracy",3),("Sharpe",3),("Return(%)",2),("MaxDD(%)",2)]:
        if c in tbl.columns:
            tbl[c] = pd.to_numeric(tbl[c], errors="coerce").round(d)

    fig2 = go.Figure(data=[go.Table(
        header=dict(values=list(tbl.columns), fill_color='paleturquoise', align='left'),
        cells=dict(values=[tbl[c] for c in tbl.columns], fill_color='lavender', align='left')
    )])
    fig2.update_layout(title="Backtest Performance Summary")
    fig2.show()

    # Optional exports
    try:
        from IPython.display import display, FileLink
        tbl.to_csv("backtest_summary.csv", index=False)
        display(FileLink("backtest_summary.csv"))
        with pd.ExcelWriter("backtest_summary.xlsx", engine="xlsxwriter") as w:
            tbl.to_excel(w, index=False, sheet_name="Summary")
        display(FileLink("backtest_summary.xlsx"))
    except Exception:
        pass
else:
    print("No backtest rows generated.")



🔵 Backtesting: EURUSD
✅ EURUSD: acc=0.969 | ret=8.26% | sharpe=3.75 | maxDD=-1.40%
Confusion matrix (rows=true, cols=pred, order [0,1,2]):
 [[  74   45    0]
 [   0 4696    0]
 [   0  110   25]]

✅ Full Backtest Results for EURUSD:
Accuracy=0.97, Return=0.08%, Sharpe=3.75
Start                         2024-11-04 07:00:00+00:00
End                           2025-08-21 16:00:00+00:00
Period                                206 days 06:00:00
Start Value                                     10000.0
End Value                                  10825.616572
Total Return [%]                               8.256166
Benchmark Return [%]                           6.608884
Max Gross Exposure [%]                            100.0
Total Fees Paid                               37.371507
Max Drawdown [%]                               1.401036
Max Drawdown Duration                  30 days 23:00:00
Total Trades                                          9
Total Closed Trades                                   


🔵 Backtesting: GBPUSD
✅ GBPUSD: acc=0.994 | ret=27.13% | sharpe=6.05 | maxDD=-2.24%
Confusion matrix (rows=true, cols=pred, order [0,1,2]):
 [[  78   17    0]
 [   1 4784    0]
 [   0   11   59]]

✅ Full Backtest Results for GBPUSD:
Accuracy=0.99, Return=0.27%, Sharpe=6.05
Start                         2024-11-04 07:00:00+00:00
End                           2025-08-21 16:00:00+00:00
Period                                206 days 06:00:00
Start Value                                     10000.0
End Value                                  12713.325869
Total Return [%]                              27.133259
Benchmark Return [%]                            3.46343
Max Gross Exposure [%]                            100.0
Total Fees Paid                               67.596185
Max Drawdown [%]                                2.24282
Max Drawdown Duration                  23 days 02:00:00
Total Trades                                         16
Total Closed Trades                                  


🔵 Backtesting: AUDUSD
✅ AUDUSD: acc=0.894 | ret=0.14% | sharpe=0.08 | maxDD=-8.01%
Confusion matrix (rows=true, cols=pred, order [0,1,2]):
 [[   0  169   16]
 [   0 4397  174]
 [   0  166   28]]

✅ Full Backtest Results for AUDUSD:
Accuracy=0.89, Return=0.00%, Sharpe=0.08
Start                         2024-11-04 07:00:00+00:00
End                           2025-08-21 16:00:00+00:00
Period                                206 days 06:00:00
Start Value                                     10000.0
End Value                                  10014.061069
Total Return [%]                               0.140611
Benchmark Return [%]                          -2.482652
Max Gross Exposure [%]                            100.0
Total Fees Paid                                  1.9996
Max Drawdown [%]                               8.014907
Max Drawdown Duration                 102 days 05:00:00
Total Trades                                          1
Total Closed Trades                                   

c:\Users\moham\OneDrive\Github\ml-double-barrier-strategy2\backtest_summary.csv

## Part 3 — Optuna Hyperparameter Tuning (Per-Symbol)

**What this section does**

- Prepares a dataset with **multi-bar labels (0/1/2)** and the core feature set.
- Defines a **RandomForest** pipeline and a **TimeSeriesSplit Accuracy** objective.
- Runs **Optuna** to search hyperparameters and **maximize Accuracy**.
- Retrains the best pipeline on all data and **saves** it in the same format used by Part 2, then compares **baseline vs. tuned** performance.

**Inputs**
- Features/labels aligned to `close`, per symbol; TSCV config (`n_splits`).
- Optuna config: `n_trials`/`timeout`, sampler (e.g., TPE), pruner (e.g., Median).

**Outputs**
- Best per-symbol pipeline (`.pkl`) + feature list (`.json`) under `models/<tf>_models/`.
- Tuning report: best params, CV **Accuracy** (primary), and reference **Sharpe** from a quick backtest.

**Flow**
1. Assemble features → create labels **{0,1,2}** → drop warm-up `NaN`s.
2. Define objective(X, y): TSCV → fit RF → predict → score by **Accuracy**.
3. `study.optimize(…)` → retrieve `best_trial` and params.
4. Refit best pipeline on **all** data → persist artifacts → summarize baseline vs. tuned.

> Tips:  
> • Use `class_weight='balanced'` if classes are imbalanced.  
> • Fix `random_state` for reproducibility; log the seed used.  
> • Prefer `timeout` over very large `n_trials` if running on many symbols.  
> • You can log **Sharpe** per fold (reference only) while keeping **Accuracy** as the objective.


In [ ]:
# ----------------------------------------------------------------------------
# FINAL PRO VERSION (updated for 0/1/2 labels): Multi-Symbol Optimization
# ----------------------------------------------------------------------------

import warnings, time, threading
from pathlib import Path
import numpy as np
import pandas as pd
import optuna
import joblib

from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.base import clone

warnings.filterwarnings("ignore")

# --- our modules ---
from ctrader_client import init_client, get_ohlc_data, symbol_name_to_id
from feature_engineering import add_core_features
from labeling_schemes import create_labels_double_barrier
from twisted.internet import reactor

# ======================
# 0) CONFIG
# ======================
symbols   = ["EURUSD", "GBPUSD", "AUDUSD"]   # change as needed
tf        = "H1"                              # "M1","M5","M15","M30","H1","H4","D1"
n_bars    = 10_000
horizon   = 5
threshold = 0.005
folds     = 3
trials    = 50

# save_folder = Path("models/h1_models")        # keep consistent with Part 2 loader
save_folder = Path(f"models/{tf.lower()}_models")  # matches Part 2’s loader pattern
save_folder.mkdir(parents=True, exist_ok=True)

# core features we standardize on
core_feature_cols = [
    "sma_20","ema_20","kama_10","rsi_14","macd_diff",
    "atr_14","obv","rolling_std_20","spread","fill","amplitude",
    "autocorr_1","autocorr_5","autocorr_10","market_regime","stationary_flag"
]

# ======================
# 1) START cTRADER ONCE
# ======================
if not reactor.running:
    threading.Thread(target=init_client, daemon=True).start()

for _ in range(200):  # wait up to ~20s for symbol map to load
    if symbol_name_to_id:
        break
    time.sleep(0.1)
else:
    raise RuntimeError("cTrader client started, but symbols failed to load in time.")

# ======================
# helpers
# ======================
def candles_to_df(candles: list[dict]) -> pd.DataFrame:
    df = pd.DataFrame(candles)
    df["time"] = pd.to_datetime(df["time"], utc=True)
    df.set_index("time", inplace=True)
    return df[["open","high","low","close","volume"]].rename(columns={"volume":"tick_volume"})


def prepare_dataset(symbol: str) -> tuple[pd.DataFrame, pd.Series, list[str]]:
    """Fetch → features → Double-Barrier labels (0/1/2) → return (X, y012, used_cols)."""
    raw = get_ohlc_data(symbol, tf=tf, n=n_bars)
    df  = candles_to_df(raw["candles"])
    dfF = add_core_features(df.copy())
    dfL = create_labels_double_barrier(dfF, up=threshold, down=threshold, horizon=horizon)  # 0/1/2

    used_cols = [c for c in core_feature_cols if c in dfL.columns]
    X = dfL[used_cols].dropna()
    y012 = dfL.loc[X.index, "barrier_label"].astype(int)  # 0/1/2
    return X, y012, used_cols


"""
# Multi bar labeling scheme
def prepare_dataset(symbol: str) -> tuple[pd.DataFrame, pd.Series, list[str]]:
    """Fetch → features → labels (0/1/2) → return (X, y, used_cols)."""
    raw = get_ohlc_data(symbol, tf=tf, n=n_bars)
    df  = candles_to_df(raw["candles"])
    dfF = add_core_features(df.copy())
    dfL = create_labels_multi_bar(dfF, horizon=horizon, threshold=threshold)  # labels already 0/1/2

    used_cols = [c for c in core_feature_cols if c in dfL.columns]
    X = dfL[used_cols].dropna()
    y = dfL.loc[X.index, "multi_bar_label"].astype(int)  # already 0/1/2
    return X, y, used_cols
"""

def tscv_accuracy(pipeline: Pipeline, X: pd.DataFrame, y012: pd.Series, n_splits: int) -> float:
    """Accuracy in 3-class space (0/1/2), skipping folds with <2 classes."""
    tscv = TimeSeriesSplit(n_splits=n_splits)
    scores = []
    for tr, te in tscv.split(X):
        X_tr, X_te = X.iloc[tr], X.iloc[te]
        y_tr, y_te = y012.iloc[tr], y012.iloc[te]
        if len(np.unique(y_tr)) < 2:
            continue
        model = clone(pipeline)
        model.fit(X_tr, y_tr)
        preds = model.predict(X_te)
        scores.append(accuracy_score(y_te, preds))
    return float(np.mean(scores)) if scores else float("nan")

# ======================
# 2) OPTIMIZE PER SYMBOL
# ======================
summary_rows = []

for symbol in symbols:
    print(f"\n\n🔵 Optimizing {symbol} ({tf})")
    try:
        X, y012, used_cols = prepare_dataset(symbol)
    except Exception as e:
        print(f"⚠️ Failed to prepare dataset for {symbol}: {e}")
        continue

    if len(X) < 1000:
        print(f"⚠️ Not enough rows for {symbol} ({len(X)}), skipping.")
        continue

    # Baseline RF
    baseline_pipe = Pipeline([
        ("scaler", StandardScaler()),
        ("rf", RandomForestClassifier(
            n_estimators=200, max_depth=None, min_samples_split=2,
            max_features="sqrt", random_state=42
        ))
    ])
    baseline_acc = tscv_accuracy(baseline_pipe, X, y012, folds)
    print(f"   Baseline RF TSCV Accuracy: {baseline_acc:.4f}")

    # Optuna objective (maximize Accuracy)
    def objective(trial: optuna.Trial) -> float:
        params = {
            "n_estimators":      trial.suggest_int("n_estimators", 200, 1200, step=100),
            "max_depth":         trial.suggest_int("max_depth", 5, 40),
            "min_samples_split": trial.suggest_int("min_samples_split", 2, 20),
            "max_features":      trial.suggest_categorical("max_features", ["sqrt", "log2", 0.5, 0.8, None]),
            "class_weight":      trial.suggest_categorical("class_weight", [None, "balanced"]),
        }
        pipe = Pipeline([
            ("scaler", StandardScaler()),
            ("rf", RandomForestClassifier(**params, random_state=42)),
        ])
        acc = tscv_accuracy(pipe, X, y012, folds)
        return -1.0 if np.isnan(acc) else acc

    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=trials, show_progress_bar=False)

    best_params = study.best_params
    best_acc    = study.best_value
    print(f"   ✅ Best Optuna RF Acc: {best_acc:.4f}")
    print(f"   🔧 Params: {best_params}")

    # Retrain best on ALL data (in 0/1/2 space)
    best_pipe = Pipeline([
        ("scaler", StandardScaler()),
        ("rf", RandomForestClassifier(**best_params, random_state=42))
    ])
    best_pipe.fit(X, y012)

    # Save bundle compatible with Part 2 loader
    save_path = save_folder / f"{symbol}_{tf}_best_model.pkl"
    joblib.dump({"pipeline": best_pipe, "features": used_cols}, save_path)
    print(f"💾 Saved best model → {save_path}")

    summary_rows.append({
        "Symbol": symbol,
        "Baseline_Acc": baseline_acc,
        "Optuna_Acc": best_acc,
        "BestParams": best_params
    })

# ======================
# 3) SUMMARY
# ======================

summary_df = pd.DataFrame(summary_rows).sort_values("Optuna_Acc", ascending=False)
summary_csv = save_folder / f"summary_optuna_{tf}.csv"
summary_df.to_csv(summary_csv, index=False)

print("\n✅ Optimization complete.")
print(f"📄 Summary saved to: {summary_csv}")
try:
    from IPython.display import display
    display(summary_df)
except Exception:
    pass


In [ ]:
# =====================================
# Part 2 — VectorBT Backtesting (cTrader) — for Optuna-tuned models (Double-Barrier)
# =====================================

# --- Setup
import warnings, time, threading
from pathlib import Path
import numpy as np
import pandas as pd
import joblib
import vectorbt as vbt
import plotly.graph_objects as go
from sklearn.metrics import confusion_matrix

warnings.filterwarnings("ignore")

from ctrader_client import init_client, get_ohlc_data, symbol_name_to_id
from feature_engineering import add_core_features
from labeling_schemes import create_labels_double_barrier
from twisted.internet import reactor  # used to check/start service

# ---------- Config ----------
symbols = ["EURUSD", "GBPUSD", "AUDUSD"]   # extend as needed
tf = "H1"                                  # "M1","M5","M15","M30","H1","H4","D1"
n_bars = 5000
horizon = 5
threshold = 0.005
fees = 0.0002
init_cash = 10_000
model_folder = Path(f"models/{tf.lower()}_models")  # must match Optuna save folder

# TF → vectorbt freq
freq_map = {"M1":"1min","M5":"5min","M15":"15min","M30":"30min","H1":"1h","H4":"4h","D1":"1D"}
freq_str = freq_map.get(tf, "1h")

# ---------- Start cTrader once ----------
if not reactor.running:
    threading.Thread(target=init_client, daemon=True).start()

# wait for symbol map bootstrap (up to ~20s)
for _ in range(200):
    if symbol_name_to_id:
        break
    time.sleep(0.1)
else:
    raise RuntimeError("cTrader client started, but symbols failed to load in time.")

# ---------- helpers ----------
def load_model_bundle(path: Path):
    """Accept both {'pipeline', 'features'} and legacy {'model','scaler','features'} bundles."""
    b = joblib.load(path)
    if "pipeline" in b:
        return dict(kind="pipeline", pipeline=b["pipeline"], features=b.get("features"))
    if "model" in b and "scaler" in b:
        return dict(kind="legacy", model=b["model"], scaler=b["scaler"], features=b.get("features"))
    raise ValueError(f"Unrecognized model bundle: {path}")

def candles_to_df(candles: list[dict]) -> pd.DataFrame:
    df = pd.DataFrame(candles)
    df["time"] = pd.to_datetime(df["time"], utc=True)
    df.set_index("time", inplace=True)
    return df[["open","high","low","close","volume"]].rename(columns={"volume":"tick_volume"})

def to_signals(preds: np.ndarray) -> np.ndarray:
    """Map {0,1,2} → {-1,0,+1}; if already in {-1,0,+1}, return as-is."""
    preds = np.asarray(preds)
    uniq = set(np.unique(preds))
    return preds - 1 if uniq.issubset({0,1,2}) else preds.astype(int)

def print_full_vbt_summary(symbol: str, pf, acc: float):
    ret = float(pf.total_return())
    sr  = float(pf.sharpe_ratio())
    print(f"\n✅ Full Backtest Results for {symbol}:")
    print(f"Accuracy={acc:.2f}, Return={ret:.2f}%, Sharpe={sr:.2f}")
    print(pf.stats())

def plot_actual_vs_predicted_close(symbol: str, close: pd.Series, preds: np.ndarray, *, horizon: int = 5, step: float = 0.001):
    """Purely visual ‘predicted close’ path, shifted by horizon and nudged by signals."""
    actual_close = close.copy()
    predicted_close = actual_close.copy()
    for i in range(len(predicted_close) - horizon):
        window = preds[i: i + horizon]
        predicted_close.iloc[i + horizon] = predicted_close.iloc[i] * (1 + step * window.sum())
    predicted_close = predicted_close.shift(-horizon)

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=actual_close.index, y=actual_close, name="Actual Close",
                             mode="lines", line=dict(width=2, color="black")))
    fig.add_trace(go.Scatter(x=predicted_close.index, y=predicted_close, name="Predicted Close",
                             mode="lines", line=dict(width=4, color="#ff9900")))
    fig.update_layout(
        title=f"📈 Actual vs Predicted Close Price (horizon={horizon}) for {symbol}",
        xaxis_title="Date", yaxis_title="Price", template="plotly_white",
        height=700, legend=dict(orientation="h")
    )
    fig.show()

# ---------- Backtest loop ----------
all_rows = []

for symbol in symbols:
    print(f"\n🔵 Backtesting: {symbol}")

    bundle_path = model_folder / f"{symbol}_{tf}_best_model.pkl"
    if not bundle_path.exists():
        print(f"⚠️ No model for {symbol} at {bundle_path}, skipping.")
        continue

    bundle = load_model_bundle(bundle_path)

    # fetch candles
    try:
        raw = get_ohlc_data(symbol, tf=tf, n=n_bars)
        df = candles_to_df(raw["candles"])
    except Exception as e:
        print(f"⚠️ Data fetch failed for {symbol}: {e}")
        continue

    # features + labels (Double-Barrier 0/1/2)
    df_feat = add_core_features(df.copy())
    df_lbl  = create_labels_double_barrier(df_feat, up=threshold, down=threshold, horizon=horizon)
    label_col = "barrier_label"

    # feature set to use
    core_cols = [
        "sma_20","ema_20","kama_10","rsi_14","macd_diff",
        "atr_14","obv","rolling_std_20","spread","fill","amplitude",
        "autocorr_1","autocorr_5","autocorr_10","market_regime","stationary_flag"
    ]
    use_cols = bundle.get("features") or [c for c in core_cols if c in df_lbl.columns]

    X = df_lbl[use_cols].dropna()
    close = df_lbl.loc[X.index, "close"]

    # labels are 0/1/2
    y012 = df_lbl.loc[X.index, label_col].astype(int)

    # predictions
    if bundle["kind"] == "pipeline":
        preds_012 = bundle["pipeline"].predict(X)     # {0,1,2}
    else:
        X_scaled = bundle["scaler"].transform(X)
        preds_012 = bundle["model"].predict(X_scaled)

    preds = to_signals(preds_012)                     # {-1,0,+1}
    acc = float((preds_012 == y012).mean())           # accuracy in 0/1/2 space

    # VectorBT portfolio (long & short)
    sig = pd.Series(preds, index=close.index)

    long_entries  = (sig.shift(1).fillna(0) <= 0) & (sig > 0)
    long_exits    = sig <= 0
    short_entries = (sig.shift(1).fillna(0) >= 0) & (sig < 0)
    short_exits   = sig >= 0

    pf = vbt.Portfolio.from_signals(
        close=close,
        entries=long_entries,
        exits=long_exits,
        short_entries=short_entries,
        short_exits=short_exits,
        init_cash=init_cash,
        freq=freq_str,
        fees=fees,
    )

    # metrics & diagnostics
    total_ret = float(pf.total_return())              # decimal (0.1769 = 17.69%)
    sharpe    = float(pf.sharpe_ratio())
    max_dd    = float(pf.max_drawdown())
    cm = confusion_matrix(y012, preds_012, labels=[0,1,2])

    print(f"✅ {symbol}: acc={acc:.3f} | ret={total_ret:.2%} | sharpe={sharpe:.2f} | maxDD={max_dd:.2%}")
    print("Confusion matrix (rows=true, cols=pred, order [0,1,2]):\n", cm)

    # full summary + plots
    print_full_vbt_summary(symbol, pf, acc)
    pf.plot(title=f"{symbol} — VectorBT Backtest ({tf})").show()
    plot_actual_vs_predicted_close(symbol, close, preds, horizon=horizon, step=0.001)

    model_name = (
        bundle["pipeline"].steps[-1][1].__class__.__name__
        if bundle["kind"] == "pipeline" else bundle["model"].__class__.__name__
    )
    all_rows.append(dict(
        Symbol=symbol,
        Model=model_name,
        Accuracy=acc,
        ReturnPct=total_ret * 100.0,
        Sharpe=sharpe,
        MaxDDPct=max_dd * 100.0
    ))

# ---------- Summary visuals ----------
summary_df = pd.DataFrame(all_rows).sort_values("Sharpe", ascending=False)

if not summary_df.empty:
    # Heatmap
    piv = summary_df.pivot(index="Model", columns="Symbol", values="Sharpe")
    ann = piv.round(2)
    fig = go.Figure(data=go.Heatmap(
        z=piv.values, x=piv.columns, y=piv.index,
        colorscale="RdYlGn", zmid=0.0, colorbar=dict(title="Sharpe"),
        hovertemplate='Model: %{y}<br>Symbol: %{x}<br>Sharpe: %{z:.3f}<extra></extra>'
    ))
    for i, m in enumerate(ann.index):
        for j, s in enumerate(ann.columns):
            v = ann.iloc[i, j]
            if pd.notna(v):
                fig.add_annotation(x=s, y=m, text=f"{v:.2f}", showarrow=False,
                                   font=dict(color="black" if abs(v) < 0.5 else "white", size=11))
    fig.update_layout(title="Sharpe per Model per Symbol (VectorBT Backtest)",
                      xaxis_title="Symbol", yaxis_title="Model", width=1300, height=600)
    fig.show()

    # Interactive table
    tbl = summary_df.rename(columns={"ReturnPct":"Return(%)","MaxDDPct":"MaxDD(%)"}).copy()
    for c, d in [("Accuracy",3),("Sharpe",3),("Return(%)",2),("MaxDD(%)",2)]:
        if c in tbl.columns:
            tbl[c] = pd.to_numeric(tbl[c], errors="coerce").round(d)

    fig2 = go.Figure(data=[go.Table(
        header=dict(values=list(tbl.columns), fill_color='paleturquoise', align='left'),
        cells=dict(values=[tbl[c] for c in tbl.columns], fill_color='lavender', align='left')
    )])
    fig2.update_layout(title="Backtest Performance Summary")
    fig2.show()

    # Optional exports
    try:
        from IPython.display import display, FileLink
        tbl.to_csv("backtest_summary.csv", index=False)
        display(FileLink("backtest_summary.csv"))
        with pd.ExcelWriter("backtest_summary.xlsx", engine="xlsxwriter") as w:
            tbl.to_excel(w, index=False, sheet_name="Summary")
        display(FileLink("backtest_summary.xlsx"))
    except Exception:
        pass
else:
    print("No backtest rows generated.")
